# Gene Enrichment Analysis

In this notebook, I will characterize gene function associated with DMR and DML.

Methods:

0. Prepare for Analyses
1. Locate Files and Set Variable Paths
2. Identify Overlaps with Background
2. Obtain GOterms

## 0. Prepare for Analyses

### 0a. Set Working Directory

In [1]:
pwd

'/Users/yaamini/Documents/yaamini-virginica/notebooks'

In [2]:
cd ../analyses/

/Users/yaamini/Documents/yaamini-virginica/analyses


In [3]:
pwd

'/Users/yaamini/Documents/yaamini-virginica/analyses'

In [4]:
!mkdir 2018-12-02-Gene-Enrichment-Analysis

In [5]:
ls -F

2018-10-25-MethylKit/                2018-12-02-Gene-Enrichment-Analysis/
2018-11-01-DML-and-DMR-Analysis/     README.md


In [6]:
cd 2018-12-02-Gene-Enrichment-Analysis/

/Users/yaamini/Documents/yaamini-virginica/analyses/2018-12-02-Gene-Enrichment-Analysis


## 1. Locate Relevant Files and Set Variable Path Names

### 1a. Set Variable Path Names

Setting the variable path names allows me to reuse this script with different input files or different paths to programs without manually changing the file names each time.

In [7]:
bedtoolsDirectory = "/Users/Shared/bioinformatics/bedtools2/bin/"

In [8]:
DMLlist = "../../analyses/2018-10-25-MethylKit/2018-11-07-DML-Locations.bed"

In [9]:
DMRlist = "../../analyses/2018-10-25-MethylKit/2018-11-07-DMR-Locations.bed"

In [10]:
geneBackground = "../../analyses/2018-10-25-MethylKit/2018-11-29-Methylation-Information-Cov3.bed"

In [12]:
mRNAList = "../2018-11-01-DML-and-DMR-Analysis/C_virginica-3.0_Gnomon_mRNA.gff3"

### 1b. Confirm Variable Path Works and Characterize Files

The BEDfiles with DML and DMR can be viewed below. Columns are are the chromosome, start position, end position, strand, and fold difference with direction. The files only have DML and DMR that were at least 50% different between the two treatments (control and elevated pCO2).

In [13]:
#Previewing the files
!head {DMLlist}

NC_035780.1	346071	346073	-	50
NC_035780.1	990995	990997	-	-51
NC_035780.1	1882691	1882693	-	52
NC_035780.1	1885022	1885024	-	61
NC_035780.1	1933499	1933501	-	53
NC_035780.1	1945182	1945184	+	55
NC_035780.1	1958998	1959000	-	53
NC_035780.1	1983256	1983258	-	-69
NC_035780.1	2538924	2538926	-	-50
NC_035780.1	2541652	2541654	-	-55


In [14]:
#Counting the number of lines to count DML
!wc -l {DMLlist}

    1398 ../../analyses/2018-10-25-MethylKit/2018-11-07-DML-Locations.bed


In [15]:
!head {DMRlist}

NC_035780.1	571100	571200	DMR	58
NC_035780.1	573700	573800	DMR	52
NC_035780.1	1885000	1885100	DMR	51
NC_035780.1	1933500	1933600	DMR	53
NC_035780.1	4285700	4285800	DMR	-51
NC_035780.1	24159600	24159700	DMR	51
NC_035780.1	26629500	26629600	DMR	65
NC_035780.1	28563400	28563500	DMR	59
NC_035780.1	29883000	29883100	DMR	-55
NC_035780.1	31302900	31303000	DMR	-61


In [16]:
#Counting the number of DMR
!wc -l {DMRlist}

     162 ../../analyses/2018-10-25-MethylKit/2018-11-07-DMR-Locations.bed


In [17]:
!head {geneBackground}

NC_007175.2	147	147	+	7	0	7	134	4	130	39	0	39	99	1	98	394	5	389	9	0	9	241	4	237	623	10	613	178	8	170	15	0	15
NC_007175.2	246	246	+	3	0	3	109	1	108	26	0	26	91	0	91	306	11	295	4	0	4	208	3	205	558	11	547	183	4	179	13	0	13
NC_007175.2	257	257	+	3	0	3	134	4	130	29	0	29	110	2	108	379	0	379	5	0	5	239	0	239	669	10	659	199	7	192	20	1	19
NC_007175.2	266	266	+	3	0	3	168	2	166	39	2	37	126	4	122	458	5	453	7	0	7	293	1	292	782	6	776	244	8	236	23	0	23
NC_007175.2	473	473	+	3	0	3	112	3	109	40	0	40	114	8	106	322	10	312	5	0	5	214	3	211	614	8	606	205	7	198	17	0	17
NC_007175.2	665	665	+	7	0	7	107	2	105	44	0	44	56	0	56	358	9	349	7	0	7	212	9	203	561	11	550	244	8	236	21	0	21
NC_007175.2	685	685	-	4	0	4	108	1	107	28	0	28	129	0	129	369	2	367	4	0	4	188	8	180	538	6	532	82	5	77	6	0	6
NC_007175.2	709	709	+	5	0	5	114	3	111	46	1	45	73	6	67	377	15	362	4	0	4	259	9	250	623	18	605	242	10	232	21	0	21
NC_007175.2	710	710	-	6	0	6	122	4	118	36	1	35	134	3	131	415	2	413	4	0	4	198	1	197	636	11	625	119	2	117	10	0	10
NC_007175.2	

In [18]:
!wc -l {geneBackground}

  670301 ../../analyses/2018-10-25-MethylKit/2018-11-29-Methylation-Information-Cov3.bed


In [60]:
!head -n 1 {mRNAList}

NC_035780.1	Gnomon	mRNA	28961	33324	.	+	.	ID=rna1;Parent=gene1;Dbxref=GeneID:111126949,Genbank:XM_022471938.1;Name=XM_022471938.1;gbkey=mRNA;gene=LOC111126949;model_evidence=Supporting evidence includes similarity to: 3 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 21 samples with support for all annotated introns;product=UNC5C-like protein;transcript_id=XM_022471938.1


In [24]:
!wc -l {mRNAList}

   60201 C_virginica-3.0_Gnomon_mRNA.gff3


## 2. Calculate Percent Overlap with DML, DMR, and Gene Background

I want to know how much of the original background is represented by DML and DMR. To do this, I'll just do some simple math.

### 2a. DML

(lines in DML) / (lines in gene background)

In [24]:
(1398 / 670301) * 100

0.20856301870353766

0.2086% overlap between DML and the original background.

### 2b. DMR

(lines in DMR) / (lines in gene background)

In [25]:
(162 / 670301) * 100

0.024168246802555866

0.0242% overlap between DMR and the original background.

## 3. Obtain GOterms

## 3a. Match gene background and mRNA

To do this, I will use `intersect` from `bedtools` to identify overlap between the background and DML or DMR, then count the number of lines. [The BEDtools suite](http://bedtools.readthedocs.io/en/latest/content/bedtools-suite.html) allows me to easily find overlapping regions of different bed files.

In [36]:
! {bedtoolsDirectory}intersectBed -h


Tool:    bedtools intersect (aka intersectBed)
Version: v2.26.0
Summary: Report overlaps between two feature files.

Usage:   bedtools intersect [OPTIONS] -a <bed/gff/vcf/bam> -b <bed/gff/vcf/bam>

	Note: -b may be followed with multiple databases and/or 
	wildcard (*) character(s). 
Options: 
	-wa	Write the original entry in A for each overlap.

	-wb	Write the original entry in B for each overlap.
		- Useful for knowing _what_ A overlaps. Restricted by -f and -r.

	-loj	Perform a "left outer join". That is, for each feature in A
		report each overlap with B.  If no overlaps are found, 
		report a NULL feature for B.

	-wo	Write the original A and B entries plus the number of base
		pairs of overlap between the two features.
		- Overlaps restricted by -f and -r.
		  Only A features with overlap are reported.

	-wao	Write the original A and B entries plus the number of base
		pairs of overlap between the two features.
		- Overlapping features restricted by -f and -r.
		  However, A fea

In [26]:
! {bedtoolsDirectory}intersectBed \
-wb \
-a {geneBackground} \
-b {mRNAList} \
> 2018-12-02-Background-mRNA.txt

In [27]:
!head 2018-12-02-Background-mRNA.txt

NC_035780.1	87542	87542	+	4	4	0	11	8	3	20	16	4	15	9	6	12	10	2	11	10	1	8	6	2	10	4	6	9	7	2	4	4	0	NC_035780.1	Gnomon	mRNA	85606	95254	.	-	.	ID=rna4;Parent=gene3;Dbxref=GeneID:111112434,Genbank:XM_022449924.1;Name=XM_022449924.1;gbkey=mRNA;gene=LOC111112434;model_evidence=Supporting evidence includes similarity to: 7 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 13 samples with support for all annotated introns;product=homeobox protein Hox-B7-like;transcript_id=XM_022449924.1
NC_035780.1	100560	100560	-	13	5	8	31	11	20	16	6	10	23	17	6	25	8	17	8	0	8	21	8	13	19	6	13	41	35	6	15	0	15	NC_035780.1	Gnomon	mRNA	99840	106460	.	+	.	ID=rna5;Parent=gene4;Dbxref=GeneID:111120752,Genbank:XM_022461698.1;Name=XM_022461698.1;gbkey=mRNA;gene=LOC111120752;model_evidence=Supporting evidence includes similarity to: 10 Proteins%2C and 100%25 coverage of the annotated genomic feature by RNAseq alignments%2C including 27 samples with support for all annotated i